<a href="https://colab.research.google.com/github/aeksei/python-urban/blob/main/PythonUrban_kgiop_objects.ipynb" target="_parent"><img src="https://colab.research.google.com/assets/colab-badge.svg" alt="Open In Colab"/></a>

# Итоговый проект. Улицы. Объекты культурного наследия.

С помощью команды `!pip` устанавливаем необходимые для работы библиотеки.  
Лучше это делать в самом начале, что не искать это по всему документу.

In [1]:
!pip install folium -U
!pip install geopandas mapclassify osmnx

Looking in indexes: https://pypi.org/simple, https://us-python.pkg.dev/colab-wheels/public/simple/
     |████████████████████████████████| 95 kB 1.5 MB/s 
  Attempting uninstall: folium
    Found existing installation: folium 0.8.3
    Uninstalling folium-0.8.3:
      Successfully uninstalled folium-0.8.3
ERROR: pip's dependency resolver does not currently take into account all the packages that are installed. This behaviour is the source of the following dependency conflicts.
datascience 0.10.6 requires folium==0.2.1, but you have folium 0.12.1.post1 which is incompatible.
Looking in indexes: https://pypi.org/simple, https://us-python.pkg.dev/colab-wheels/public/simple/
     |████████████████████████████████| 1.0 MB 6.6 MB/s 
     |████████████████████████████████| 95 kB 4.3 MB/s 
     |████████████████████████████████| 6.3 MB 43.1 MB/s 
     |████████████████████████████████| 16.7 MB 273 kB/s 
     |████████████████████████████████| 1.0 MB 49.0 MB/s 
     |███████████████████████████

## Оформление Jupyter Notebook по PEP8. 

Импорт всех библиотек желательно выносить в самое начало.  



In [2]:
# библитеки, которые не входят в стандартный набор
import osmnx as ox
import pandas as pd
import geopandas as gpd

pd.options.plotting.backend = "plotly"  # необходимо для изменения отображения графиков в colab

Далее следуют константы, которые нужны на протяжении всего проекта.  
С помощью них проще управлять стилистикой или данными с которыми происходит работа.

In [3]:
# Константа, чтобы везде была одна и таже подложка карт
TILES = "CartoDB positron"

# Данные, с которыми будет идти работа в проекте
TERRITORY_NAME = 'Адмиралтейский район, Санкт-Петербург'
STREETS_FILE_URL = "https://drive.google.com/file/d/1bUT1E-QSbG1vpSNM2dOG2-LEVXSrPdo3/view?usp=sharing"
KGIOP_FILE_URL = "https://raw.githubusercontent.com/aeksei/python-urban/main/kgiop_objects.geojson"

Далее можно вынести функции, которые нужны всему проекту.  
К функция желательно (очень желательно:) ) писать документацию. 
 
Плюс использовать аннотацию типов, чтобы понимать,  
с какими типами данных работает функция.  
И какой результат возвращает.

In [4]:
def get_google_drive_download_url(url: str) -> str:
    """
    Функция возвращает ссылку для скачивания с google drive.
     Например: "https://drive.google.com/file/d/1MWGOuqV76e0ubQOg8Ke0KTU3yGpkprHp/view?usp=sharing" ->
     "https://drive.google.com/uc?export=download&id=1MWGOuqV76e0ubQOg8Ke0KTU3yGpkprHp"
    """
    drive_id = url.split("/")[5]
    return f"https://drive.google.com/uc?export=download&id={drive_id}"

## Территория

### Загрузка территории из OSM (Extract)

In [5]:
territory = ox.geocode_to_gdf(TERRITORY_NAME)  # подгружаем с OSM и получаем GeoDataFrame
territory.explore(tiles=TILES)

## Улицы

### Загрузка файла с улицами из google disk (Extract)

In [6]:
url = get_google_drive_download_url(STREETS_FILE_URL)
gdf_streets = gpd.read_file(url, mask=territory)  # фильтруем улицы по маске геометрии территории
gdf_streets

type         id                                               tags  \
0     way    4454381  {'highway': 'unclassified', 'name': 'набережна...   
1     way    4454822  {'addr:region': 'Санкт-Петербург', 'foot': 'no...   
2     way    4455260  {'foot': 'no', 'highway': 'residential', 'lane...   
3     way    4456433  {'hgv': 'destination', 'highway': 'residential...   
4     way    4456613     {'highway': 'service', 'living_street': 'yes'}   
...   ...        ...                                                ...   
8489  way  980137153       {'highway': 'service', 'surface': 'asphalt'}   
8490  way  980137155       {'highway': 'service', 'surface': 'asphalt'}   
8491  way  980137157  {'highway': 'service', 'service': 'parking_ais...   
8492  way  981628988  {'foot': 'no', 'highway': 'primary', 'lanes': ...   
8493  way  981641275  {'highway': 'service', 'oneway': 'yes', 'tunne...   

                                               geometry  
0     LINESTRING (3368853.534 8379613.768, 3368894.2...  
1     LINESTRING (3374917.530 8383417.375, 3374910.2...  
2     LINESTRING (3372221.049 8381344.575, 3372211.4...  
3     LINESTRING (3369358.324 8379129.066, 3369358.6...  
4     LINESTRING (3373919.996 8384107.727, 3373916.6...  
...                                                 ...  
8489  LINESTRING (3377531.379 8381480.181, 3377526.0...  
8490  LINESTRING (3377527.961 8381478.182, 3377531.3...  
8491  LINESTRING (3377380.285 8381274.086, 3377410.2...  
8492  LINESTRING (3372247.866 8383962.454, 3372262.3...  
8493  LINESTRING (3375298.310 8383126.591, 3375338.2...  

[8494 rows x 4 columns]

### Обработка данных с улицами (Transform)

[json_normalize](https://pandas.pydata.org/docs/reference/api/pandas.json_normalize.html) позволяет преобразовать  
вложенные структуры данных в json файле с таблицу.

In [7]:
tags = pd.json_normalize(gdf_streets["tags"])
tags

highway                         name                      name:ru  \
0     unclassified  набережная Обводного канала  набережная Обводного канала   
1          primary            переулок Гривцова            переулок Гривцова   
2      residential          Люблинский переулок                          NaN   
3      residential               Бумажная улица                          NaN   
4          service                          NaN                          NaN   
...            ...                          ...                          ...   
8489       service                          NaN                          NaN   
8490       service                          NaN                          NaN   
8491       service                          NaN                          NaN   
8492       primary    набережная Крюкова канала                          NaN   
8493       service                          NaN                          NaN   

          addr:region foot   int_ref lanes  lit  maxspeed          old_name  \
0                 NaN  NaN       NaN   NaN  NaN       NaN               NaN   
1     Санкт-Петербург   no  E 95;AH8     2  yes  RU:urban  Демидов переулок   
2                 NaN   no       NaN     2  yes  RU:urban               NaN   
3                 NaN  NaN       NaN     2  yes  RU:urban               NaN   
4                 NaN  NaN       NaN   NaN  NaN       NaN               NaN   
...               ...  ...       ...   ...  ...       ...               ...   
8489              NaN  NaN       NaN   NaN  NaN       NaN               NaN   
8490              NaN  NaN       NaN   NaN  NaN       NaN               NaN   
8491              NaN  NaN       NaN   NaN  NaN       NaN               NaN   
8492              NaN   no       NaN     2  yes        40               NaN   
8493              NaN  NaN       NaN   NaN  NaN       NaN               NaN   

      ... level noname maxweight:signed name:et footway oneway:psv barrier  \
0     ...   NaN    NaN              NaN     NaN     NaN        NaN     NaN   
1     ...   NaN    NaN              NaN     NaN     NaN        NaN     NaN   
2     ...   NaN    NaN              NaN     NaN     NaN        NaN     NaN   
3     ...   NaN    NaN              NaN     NaN     NaN        NaN     NaN   
4     ...   NaN    NaN              NaN     NaN     NaN        NaN     NaN   
...   ...   ...    ...              ...     ...     ...        ...     ...   
8489  ...   NaN    NaN              NaN     NaN     NaN        NaN     NaN   
8490  ...   NaN    NaN              NaN     NaN     NaN        NaN     NaN   
8491  ...   NaN    NaN              NaN     NaN     NaN        NaN     NaN   
8492  ...   NaN    NaN              NaN     NaN     NaN        NaN     NaN   
8493  ...   NaN    NaN              NaN     NaN     NaN        NaN     NaN   

     noexit incline sidewalk  
0       NaN     NaN      NaN  
1       NaN     NaN      NaN  
2       NaN     NaN      NaN  
3       NaN     NaN      NaN  
4       NaN     NaN      NaN  
...     ...     ...      ...  
8489    NaN     NaN      NaN  
8490    NaN     NaN      NaN  
8491    NaN     NaN      NaN  
8492    NaN     NaN      NaN  
8493    NaN     NaN      NaN  

[8494 rows x 82 columns]

In [8]:
tags.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 8494 entries, 0 to 8493
Data columns (total 82 columns):
 #   Column               Non-Null Count  Dtype 
---  ------               --------------  ----- 
 0   highway              8494 non-null   object
 1   name                 1201 non-null   object
 2   name:ru              614 non-null    object
 3   addr:region          3 non-null      object
 4   foot                 1351 non-null   object
 5   int_ref              151 non-null    object
 6   lanes                1162 non-null   object
 7   lit                  1212 non-null   object
 8   maxspeed             1187 non-null   object
 9   old_name             193 non-null    object
 10  surface              1965 non-null   object
 11  hgv                  41 non-null     object
 12  postal_code          174 non-null    object
 13  living_street        794 non-null    object
 14  access               724 non-null    object
 15  oneway               931 non-null    object
 16  wikida

Из всех тегов оставим только теги `name` и `name:ru`.  
И прицепим их к улицам с помощью метода `join`.  
По умолчанию сопоставление происходит по столбцу с индексами.

In [9]:
extract_tags = [
    "name", 
]

gdf_streets = gdf_streets.join(tags[extract_tags])
gdf_streets

type         id                                               tags  \
0     way    4454381  {'highway': 'unclassified', 'name': 'набережна...   
1     way    4454822  {'addr:region': 'Санкт-Петербург', 'foot': 'no...   
2     way    4455260  {'foot': 'no', 'highway': 'residential', 'lane...   
3     way    4456433  {'hgv': 'destination', 'highway': 'residential...   
4     way    4456613     {'highway': 'service', 'living_street': 'yes'}   
...   ...        ...                                                ...   
8489  way  980137153       {'highway': 'service', 'surface': 'asphalt'}   
8490  way  980137155       {'highway': 'service', 'surface': 'asphalt'}   
8491  way  980137157  {'highway': 'service', 'service': 'parking_ais...   
8492  way  981628988  {'foot': 'no', 'highway': 'primary', 'lanes': ...   
8493  way  981641275  {'highway': 'service', 'oneway': 'yes', 'tunne...   

                                               geometry  \
0     LINESTRING (3368853.534 8379613.768, 3368894.2...   
1     LINESTRING (3374917.530 8383417.375, 3374910.2...   
2     LINESTRING (3372221.049 8381344.575, 3372211.4...   
3     LINESTRING (3369358.324 8379129.066, 3369358.6...   
4     LINESTRING (3373919.996 8384107.727, 3373916.6...   
...                                                 ...   
8489  LINESTRING (3377531.379 8381480.181, 3377526.0...   
8490  LINESTRING (3377527.961 8381478.182, 3377531.3...   
8491  LINESTRING (3377380.285 8381274.086, 3377410.2...   
8492  LINESTRING (3372247.866 8383962.454, 3372262.3...   
8493  LINESTRING (3375298.310 8383126.591, 3375338.2...   

                             name  
0     набережная Обводного канала  
1               переулок Гривцова  
2             Люблинский переулок  
3                  Бумажная улица  
4                             NaN  
...                           ...  
8489                          NaN  
8490                          NaN  
8491                          NaN  
8492    набережная Крюкова канала  
8493                          NaN  

[8494 rows x 5 columns]

Удалим те улицы, у которых нет названия.  
По умолчанию `dropna` удаляет строки,  
у которых отсутствует хотя бы одно значение. 

Мы же хотим удалить строки, в которых отсутствует  
значение сразу в двух столбцах: `name` и `name:ru`. 

In [10]:
gdf_streets.dropna(
    how="all",  # удалить если отсутствуют значения во всех указанных столбцах
    subset=["name"],  # столбцы, в которых надо искать пропуски
    inplace=True
)
gdf_streets

type         id                                               tags  \
0     way    4454381  {'highway': 'unclassified', 'name': 'набережна...   
1     way    4454822  {'addr:region': 'Санкт-Петербург', 'foot': 'no...   
2     way    4455260  {'foot': 'no', 'highway': 'residential', 'lane...   
3     way    4456433  {'hgv': 'destination', 'highway': 'residential...   
5     way    4457206  {'foot': 'no', 'highway': 'residential', 'lane...   
...   ...        ...                                                ...   
8479  way  976951047  {'highway': 'unclassified', 'lit': 'yes', 'max...   
8480  way  976951048  {'highway': 'unclassified', 'lit': 'yes', 'max...   
8482  way  976974609  {'highway': 'tertiary', 'lanes': '2', 'lit': '...   
8486  way  978525440  {'cycleway:right': 'lane', 'foot': 'no', 'high...   
8492  way  981628988  {'foot': 'no', 'highway': 'primary', 'lanes': ...   

                                               geometry  \
0     LINESTRING (3368853.534 8379613.768, 3368894.2...   
1     LINESTRING (3374917.530 8383417.375, 3374910.2...   
2     LINESTRING (3372221.049 8381344.575, 3372211.4...   
3     LINESTRING (3369358.324 8379129.066, 3369358.6...   
5     LINESTRING (3372683.994 8380856.184, 3372703.9...   
...                                                 ...   
8479  LINESTRING (3374305.629 8376701.087, 3374290.3...   
8480  LINESTRING (3374263.773 8376690.877, 3374279.6...   
8482  LINESTRING (3374321.804 8378141.245, 3374321.6...   
8486  LINESTRING (3375466.001 8382603.187, 3375113.7...   
8492  LINESTRING (3372247.866 8383962.454, 3372262.3...   

                             name  
0     набережная Обводного канала  
1               переулок Гривцова  
2             Люблинский переулок  
3                  Бумажная улица  
5      13-я Красноармейская улица  
...                           ...  
8479  Малая Митрофаньевская улица  
8480  Малая Митрофаньевская улица  
8482           Парфёновская улица  
8486     набережная реки Фонтанки  
8492    набережная Крюкова канала  

[1201 rows x 5 columns]

Проверим наличие дубликатов

In [11]:
gdf_streets.duplicated(subset=["id", "geometry", "name"]).value_counts()

False    1201
dtype: int64

Проверим, являются ли названия улиц уникальными.

In [12]:
gdf_streets["name"].is_unique

False

Тогда с помощью метода [dissolve](https://geopandas.org/en/stable/docs/user_guide/aggregation_with_dissolve.html#dissolve-example) сгруппируем геометрии по столбцу `name` и объединим геометрии в одну

In [13]:
gdf_streets = gdf_streets.dissolve(by="name")
gdf_streets

geometry  \
name                                                                            
1-й мост Круштейна          MULTILINESTRING ((3371922.223 8384393.995, 337...   
1-я Красноармейская улица   MULTILINESTRING ((3373826.198 8381061.512, 337...   
10-я Красноармейская улица  MULTILINESTRING ((3372133.931 8380334.118, 337...   
11-я Красноармейская улица  MULTILINESTRING ((3373790.832 8380234.239, 337...   
12-я Красноармейская улица  MULTILINESTRING ((3372708.718 8380047.963, 337...   
...                                                                       ...   
улица Степана Разина        MULTILINESTRING ((3369019.100 8379612.857, 336...   
улица Труда                 LINESTRING (3372477.752 8383885.875, 3372458.3...   
улица Циолковского          MULTILINESTRING ((3371725.332 8379587.412, 337...   
улица Шкапина               MULTILINESTRING ((3371901.952 8378076.225, 337...   
улица Якубовича             MULTILINESTRING ((3372303.559 8384400.683, 337...   

                           type         id  \
name                                         
1-й мост Круштейна          way  122236934   
1-я Красноармейская улица   way  141966303   
10-я Красноармейская улица  way  404661532   
11-я Красноармейская улица  way   31366311   
12-я Красноармейская улица  way   31368568   
...                         ...        ...   
улица Степана Разина        way   23591680   
улица Труда                 way  147142206   
улица Циолковского          way   31386622   
улица Шкапина               way  326728921   
улица Якубовича             way  146724995   

                                                                         tags  
name                                                                           
1-й мост Круштейна          {'highway': 'service', 'name': '1-й мост Крушт...  
1-я Красноармейская улица   {'foot': 'no', 'highway': 'secondary', 'lanes'...  
10-я Красноармейская улица  {'foot': 'no', 'highway': 'tertiary', 'lanes':...  
11-я Красноармейская улица  {'foot': 'no', 'highway': 'residential', 'lane...  
12-я Красноармейская улица  {'foot': 'no', 'highway': 'tertiary', 'lanes':...  
...                                                                       ...  
улица Степана Разина        {'foot': 'no', 'highway': 'tertiary', 'lanes':...  
улица Труда                 {'foot': 'no', 'highway': 'primary', 'lanes': ...  
улица Циолковского          {'foot': 'no', 'hgv': 'destination', 'highway'...  
улица Шкапина               {'foot': 'no', 'highway': 'secondary', 'lanes'...  
улица Якубовича             {'foot': 'no', 'highway': 'residential', 'lane...  

[218 rows x 4 columns]

In [14]:
gdf_streets.index.rename("Название улицы", inplace=True)
gdf_streets.head()

geometry  \
Название улицы                                                                  
1-й мост Круштейна          MULTILINESTRING ((3371922.223 8384393.995, 337...   
1-я Красноармейская улица   MULTILINESTRING ((3373826.198 8381061.512, 337...   
10-я Красноармейская улица  MULTILINESTRING ((3372133.931 8380334.118, 337...   
11-я Красноармейская улица  MULTILINESTRING ((3373790.832 8380234.239, 337...   
12-я Красноармейская улица  MULTILINESTRING ((3372708.718 8380047.963, 337...   

                           type         id  \
Название улицы                               
1-й мост Круштейна          way  122236934   
1-я Красноармейская улица   way  141966303   
10-я Красноармейская улица  way  404661532   
11-я Красноармейская улица  way   31366311   
12-я Красноармейская улица  way   31368568   

                                                                         tags  
Название улицы                                                                 
1-й мост Круштейна          {'highway': 'service', 'name': '1-й мост Крушт...  
1-я Красноармейская улица   {'foot': 'no', 'highway': 'secondary', 'lanes'...  
10-я Красноармейская улица  {'foot': 'no', 'highway': 'tertiary', 'lanes':...  
11-я Красноармейская улица  {'foot': 'no', 'highway': 'residential', 'lane...  
12-я Красноармейская улица  {'foot': 'no', 'highway': 'tertiary', 'lanes':...

Удалим ненужные столбцы из датафрейма с улицами.

In [15]:
drop_columns = [
    "id",
    "type", 
    "tags",
]
gdf_streets.drop(columns=drop_columns, inplace=True)
gdf_streets.head()

geometry
Название улицы                                                               
1-й мост Круштейна          MULTILINESTRING ((3371922.223 8384393.995, 337...
1-я Красноармейская улица   MULTILINESTRING ((3373826.198 8381061.512, 337...
10-я Красноармейская улица  MULTILINESTRING ((3372133.931 8380334.118, 337...
11-я Красноармейская улица  MULTILINESTRING ((3373790.832 8380234.239, 337...
12-я Красноармейская улица  MULTILINESTRING ((3372708.718 8380047.963, 337...

In [16]:
gdf_streets.explore(tiles=TILES)

## Объекты культурного наследия

### Загрузка объектов культурного наследия из github?

In [17]:
gdf_kgiop_objects = gpd.read_file(KGIOP_FILE_URL, mask=territory)
gdf_kgiop_objects

id ensemble_name                                        object_name  \
0        1             —  Здание Консисторского управления Могилевской Р...   
1        2             —  Здание манежа (экзерциргауса) лейб-гвардии Изм...   
2        3             —  Дом, где в начале 1895 г. Ленин В.И. встречалс...   
3        4             —                        Трансформаторная подстанция   
4        5             —  Манеж графа Г.И. Рибопьера (Здание Санкт-Петер...   
...    ...           ...                                                ...   
1017  9601             —                       Здание (многоквартирный дом)   
1018  9602             —                       Здание (многоквартирный дом)   
1019  9608             —  Участок сохранившегося культурного слоя, вмеща...   
1020  9624             —  Депо комплекса построек Товарной станции Варша...   
1021  9626             —  Пряжка 1. Участок культурного слоя города Санк...   

                                 occurrence_time  \
0     1870-1873; 1878-1879; 1896-1897; 1900-1902   
1                                      1795-1797   
2                                              —   
3                                      1906-1907   
4                                     1887; 1891   
...                                          ...   
1017                                   1857-1858   
1018                                        1866   
1019                                           —   
1020                                           —   
1021                                           —   

                                        object_location  \
0                1-я Красноармейская ул., 11, лит. А, Б   
1     1-я Красноармейская ул., 13; Измайловский пр.,...   
2                           1-я Красноармейская ул., 22   
3                          11-я Красноармейская ул., 28   
4                           2-я Красноармейская ул., 12   
...                                                 ...   
1017                      Фонтанки р. наб., 128, лит. А   
1018                      Фонтанки р. наб., 132, лит. З   
1019  квартал, образованный пер. Бойцова, наб. р. Фо...   
1020         Обводного кан. наб., 118, корп. 12, лит. Ч   
1021                                      Мясная ул., 3   

                                    historical_category  \
0     объект культурного наследия регионального знач...   
1     объект культурного наследия регионального знач...   
2     объект культурного наследия регионального знач...   
3     объект культурного наследия регионального знач...   
4     объект культурного наследия регионального знач...   
...                                                 ...   
1017             выявленный объект культурного наследия   
1018             выявленный объект культурного наследия   
1019             выявленный объект культурного наследия   
1020             выявленный объект культурного наследия   
1021             выявленный объект культурного наследия   

                                          normative_act object_type  \
0              Распоряжение КГИОП № 10-22 от 21.07.2009    Памятник   
1         Закон Санкт-Петербурга № 141-47 от 02.07.1997    Памятник   
2         Закон Санкт-Петербурга № 141-47 от 02.07.1997    Памятник   
3     Решение исполкома Ленгорсовета № 963 от 05.12....    Памятник   
4              Распоряжение КГИОП № 10-26 от 15.09.2009    Памятник   
...                                                 ...         ...   
1017           Распоряжение КГИОП от 17.06.2019 № 289-р    Памятник   
1018           Распоряжение КГИОП от 17.06.2019 № 290-р    Памятник   
1019           Распоряжение КГИОП от 06.08.2019 № 450-р    Памятник   
1020           Распоряжение КГИОП от 22.08.2019 № 507-р    Памятник   
1021           Распоряжение КГИОП от 03.09.2019 № 522-р    Памятник   

                             geometry  
0     POINT (3374338.001 8381192.049)  
1     POINT (3373995.026 8381101.886)  
2     POINT (3374182.710 8381041.925)  
3  

In [18]:
gdf_kgiop_objects.explore(tiles=TILES)

In [19]:
STREET_BUFFER = 100

def get_contains_kgiop_objects(street) -> int:
    """ Функция для подсчета количества объектов культурного наследия попадающих в буффер улицы"""
    return sum(gdf_kgiop_objects["geometry"].within(street.buffer(STREET_BUFFER)))


gdf_streets["contains_kgiop_objects"] = gdf_streets["geometry"].apply(get_contains_kgiop_objects)
gdf_streets.nlargest(5, "contains_kgiop_objects")

geometry  \
Название улицы                                                                    
набережная канала Грибоедова  MULTILINESTRING ((3372782.378 8382201.669, 337...   
набережная реки Фонтанки      MULTILINESTRING ((3375953.581 8382975.162, 337...   
набережная реки Мойки         MULTILINESTRING ((3371360.349 8383879.121, 337...   
Садовая улица                 MULTILINESTRING ((3372431.087 8381889.256, 337...   
Галерная улица                MULTILINESTRING ((3372046.801 8384726.444, 337...   

                              contains_kgiop_objects  
Название улицы                                        
набережная канала Грибоедова                      78  
набережная реки Фонтанки                          63  
набережная реки Мойки                             45  
Садовая улица                                     40  
Галерная улица                                    36

In [20]:
gdf_streets.explore("contains_kgiop_objects", tiles=TILES)

In [21]:
m = gdf_streets.explore("contains_kgiop_objects", tiles=TILES)
m = territory.explore(m=m, style_kwds={"fill": False, "weight": 5})
m = gdf_kgiop_objects.explore(m=m, color="red")

m

In [22]:
gdf_streets["density"] = gdf_streets["contains_kgiop_objects"] / gdf_streets.length

select_columns = []
gdf_streets.nlargest(5, "density")

geometry  \
Название улицы                                                             
Адмиралтейский мост    LINESTRING (3371173.188 8384227.299, 3371189.9...   
2-й мост Круштейна     MULTILINESTRING ((3371488.155 8384073.003, 337...   
Подьяческий мост       MULTILINESTRING ((3373613.645 8383456.806, 337...   
Торговый мост          LINESTRING (3372486.457 8382954.037, 3372526.4...   
Старо-Никольский мост  MULTILINESTRING ((3372893.464 8382096.034, 337...   

                       contains_kgiop_objects   density  
Название улицы                                           
Адмиралтейский мост                         3  0.158629  
2-й мост Круштейна                          3  0.084806  
Подьяческий мост                            3  0.079259  
Торговый мост                               3  0.068534  
Старо-Никольский мост                       3  0.066640

In [23]:
gdf_streets.to_file('streets_with_contains_kgiop.geojson', driver='GeoJSON')

## Немножко статистики...

In [24]:
len(gdf_kgiop_objects) / gdf_streets.length.sum() # средняя плотность

0.003202048532236554

In [25]:
gdf_streets["contains_kgiop_objects"].describe()

count    218.000000
mean       6.440367
std        9.864923
min        0.000000
25%        1.000000
50%        3.000000
75%        7.000000
max       78.000000
Name: contains_kgiop_objects, dtype: float64

In [26]:
gdf_streets["contains_kgiop_objects"].sort_values(ascending=False).plot.bar()